In [18]:
import folium
from folium import plugins
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
import numpy as np
%matplotlib inline

In [19]:
m = folium.Map([35.681382, 139.76608399999998], zoom_start=11)
m


In [20]:
import pandas as pd
import re
import glob
import json
from collections import namedtuple

Datum = namedtuple('Data', ['origin', 'latlng', 'chingin', 'name', 'desc'])
Data = []

origingeo_latlng = {}
for fn in glob.glob('./geos/*.json'):
    obj = json.load(open(fn))
    try:
        origin = obj['OriginGeo']
    except Exception as ex:
        #print(ex)
        #print(obj)
        continue
    latlng = (obj['results'][-1]['geometry']['location'])
    #print(origin, latlng)
    origingeo_latlng[origin] = latlng
#exit()

df = pd.read_csv('./local.csv')
df = df[pd.notna(df['賃金 賃金形態'])]
df = df[pd.notna(df['所在地'])]
df = df[pd.notnull(df['賃金 賃金形態'])]
def parse_chingin(x):
    chingin = None
    try:
        chingin = re.search(r'a \+ b (\d{1,},\d{1,})円', x).group(1)
    except Exception as ex:
        print(ex)
    return chingin
for chingin, origin, name, desc in zip(df['賃金 賃金形態'], df['所在地'], df['事業所名'], df['事業内容']):
    if pd.isna(origin):
        continue
    if origingeo_latlng.get(origin) is None:
        continue
    chingin = parse_chingin(chingin)
    
    if chingin is None:
        continue

    Data.append( Datum(origin=origin, latlng=origingeo_latlng[origin], chingin=chingin, name=name, desc=desc ) )

'NoneType' object has no attribute 'group'


In [21]:
arr = np.array([[float(d.latlng['lat']),float(d.latlng['lng']), int(d.chingin.replace(',', ''))/10000] for d in Data])
arr

array([[ 36.190732 , 139.942048 ,  16.416    ],
       [ 40.8029079, 140.7058672,  17.098    ],
       [ 37.4132829, 138.8308027,  17.205    ],
       ...,
       [ 35.4148102, 136.7603328,  18.9      ],
       [ 37.9181333, 139.0690841,  20.0383   ],
       [ 33.260193 , 130.55479  ,  15.4      ]])

In [22]:
%%javascript
IPython.OutputArea.auto_scroll_threshold = 9999;



<IPython.core.display.Javascript object>

In [23]:
m = folium.Map([35.681382, 139.76608399999998], prefer_canvas=True, zoom_start=10)

m.add_children(plugins.HeatMap(arr, radius=8))
m

/home/gimpei/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:3: FutureWarning: Method `add_children` is deprecated. Please use `add_child` instead.
  This is separate from the ipykernel package so we can avoid doing imports until


In [24]:
%%javascript
var x = document.getElementById("demo");
function getLocation() {
  if (navigator.geolocation) {
    navigator.geolocation.getCurrentPosition(showPosition);
  } else {
    x.innerHTML = "Geolocation is not supported by this browser.";
  }
}

function showPosition(position) {
  x.innerHTML = "Latitude: " + position.coords.latitude + 
  "<br>Longitude: " + position.coords.longitude; 
}
element.text(getLocation());

<IPython.core.display.Javascript object>

In [25]:

lat, lng = [35.6592, 139.7057]
m = folium.Map([lat, lng],prefer_canvas=True, zoom_start=15)


In [26]:
m

In [27]:
color_defs = {
    0: '#4277f4',
    1: '#41c1f4',
    2:'#41c1f4',
    3:'#41c1f4',
    4:'#41f4d3',
    5:'#41f497',
    6:'#acf441',
    7:'#dcf441',
    8:'#f4d041',
    9:'#f49741',
    10:'#f47641',
    11:'#f44141'

}

# DataSort
def sort(d):
    return abs(d.latlng['lat'] - lat) + abs(d.latlng['lng'] - lng)
Data = sorted(Data, key=sort)[:1000]
    

for idx, d in enumerate(Data):
    #print(idx)
    lat, lng, chingin, name, desc = float(d.latlng['lat']),float(d.latlng['lng']), int(d.chingin.replace(',', ''))//28000, d.name, d.desc
    popup=folium.Popup(f'Name: {name} <br>'
                     f'Money: {28000*chingin}<br>'
                     f'事業内容: {desc}', max_width=1000, show=False)
    try:
        folium.CircleMarker(
            [lat, lng],
            radius=5,
            popup = popup,
            color=color_defs[chingin],
            fill_color=color_defs[chingin], #colordict[traffic_q],
            fill=True,
            fill_opacity=1
            ).add_to(m)
    except Exception as ex:
        folium.CircleMarker(
            [lat, lng],
            radius=5,
            popup = popup,
            color="red",
            fill_color="red", 
            fill=True,
            fill_opacity=1
        ).add_to(m)
    
m

In [28]:
m.save('sample_output.html')


In [29]:
m

In [30]:
color_defs = {
    0: '#4277f4',
    1: '#41c1f4',
    2:'#41c1f4',
    3:'#41c1f4',
    4:'#41f4d3',
    5:'#41f497',
    6:'#acf441',
    7:'#dcf441',
    8:'#f4d041',
    9:'#f49741',
    10:'#f47641',
    11:'#f44141'

}

# DataSort
def sort(d):
    return abs(d.latlng['lat'] - lat) + abs(d.latlng['lng'] - lng)
Data = sorted(Data, key=sort)

for idx, d in enumerate(Data):
    #print(idx)
    lat, lng, chingin, name, desc = float(d.latlng['lat']),float(d.latlng['lng']), int(d.chingin.replace(',', ''))//28000, d.name, d.desc
    popup=folium.Popup(f'Name: {name} <br>'
                     f'Money: {28000*chingin}<br>'
                     f'事業内容: {desc}', max_width=1000, show=False)
    try:
        folium.CircleMarker(
            [lat, lng],
            radius=5,
            popup = popup,
            color=color_defs[chingin],
            fill_color=color_defs[chingin], #colordict[traffic_q],
            fill=True,
            fill_opacity=1
            ).add_to(m)
    except Exception as ex:
        folium.CircleMarker(
            [lat, lng],
            radius=5,
            popup = popup,
            color="red",
            fill_color="red", 
            fill=True,
            fill_opacity=1
        ).add_to(m)
    
m.save('sample_output_total.html')